# Tradingview to vectorbt backtest analysis

In [1]:
from numpy import sort
import vectorbt as vbt
import pandas as pd 
import datetime, pytz
from datetime import datetime, timedelta

# Read In Data

In [2]:
start_date = datetime(2018, 1, 1, tzinfo=pytz.utc)  # time period for analysis, must be timezone-aware
# end_date = datetime.now(pytz.utc)
# end_date = datetime(2020, 1, 1, tzinfo=pytz.utc)
# The following is the number of days to look back for the analysis
# time_buffer = timedelta(days=100)  # buffer before to pre-calculate SMA/EMA, best to set to max window
vbt.settings.portfolio['init_cash'] = 100_000.  # 100,000$
vbt.settings.portfolio['fees'] = 0.0025  # 0.25% # These may already be incorporated into trade file 
# vbt.settings.portfolio['commission'] = 0.0025  # 0.25% May want to use this later

# Read in the Trade File from Tradingview Strategy

In [28]:
# Download trade file from tradingview strategy as csv
trade_file_2hr = "./data/eth_2h_low_dd.csv"

df_trades_2hr = pd.read_csv(trade_file_2hr)
# df_trades_2hr = pd.read_csv(trade_file_90m)

# Download Data to match the same raw price series that you were using in tradingview
The following cell we get binance data to match the tradingview data. Using the vectorbt function allows for you to update your data rather than re-downloading it. Use same frequency and ticker/exchange as what you used in your tradingview strategy for consistency

In [29]:
# If you would like to update the data, you can do it here
binance_data_30m.update(show_progress=True)
binance_data_2hr.update(show_progress=True)
print("Updated data")
binance_data_2hr.save("./data/BINANCE_ETHUSDT_2h.pickle")
binance_data_30m.save("./data/BINANCE_ETHUSDT_30m.pickle")
print("Saved data")

2022-02-25 06:00:00+00:00 - 2022-02-25 06:30:00+00:00: : 1it [00:00,  1.31it/s]
2022-02-25 06:00:00+00:00 - 2022-02-25 06:00:00+00:00: : 1it [00:00,  1.29it/s]

Updated data
Saved data


In [30]:
symbol = "ETHUSDT"
freq = '30m' 
# Note, binance doesn't support 90m data, so we're will need to do 30 min data and convert
# See here for the constants https://python-binance.readthedocs.io/en/latest/constants.html
binance_data_30m = vbt.BinanceData.download(symbol, start=start_date, end="now UTC", interval='30m', show_progress=True) 
binance_data_2hr = vbt.BinanceData.download(symbol, start=start_date, end="now UTC", interval='2h', show_progress=True)

# Now pull in the 2hour data
try: 
    binance_data_2hr.load("./data/BINANCE_ETHUSDT_2h.pickle")
    print("Loaded 2hr data from file")
except: 
    print("loading data from pickle failed")
    binance_data_2hr.get() # get data from binance first time can comment this out if you want to use the data from the csv
    binance_data_2hr.save("./data/BINANCE_ETHUSDT_2h.pickle") # save data to file this is a pickle file 


# Now pull in the 30m data
try: 
    binance_data_30m.load("./data/BINANCE_ETHUSDT_30m.pickle")
    print("Loaded 30m data from file")
except: 
    print("loading data from pickle failed")
    binance_data_30m.get() # get data from binance first time can comment this out if you want to use the data from the csv
    binance_data_30m.save("./data/BINANCE_ETHUSDT_30m.pickle") # save data to file this is a pickle file 

# Now set the dataframes to the underlying assets
df_data_2hr = binance_data_2hr.data["ETHUSDT"] # get the dataframe from the binance data object
df_data_30m = binance_data_30m.data["ETHUSDT"] # get the dataframe from the binance data object



2018-01-01 00:00:00+00:00 - 2022-02-25 06:30:00+00:00: : 146it [01:43,  1.41it/s]
2018-01-01 00:00:00+00:00 - 2022-02-25 06:00:00+00:00: : 37it [00:27,  1.35it/s]

Loaded 2hr data from file
Loaded 30m data from file


# Create a 90 minute dataframe

In [31]:
print(df_data_30m.columns)



Index(['Open', 'High', 'Low', 'Close', 'Volume', 'Close time', 'Quote volume',
       'Number of trades', 'Taker base volume', 'Taker quote volume'],
      dtype='object')


In [32]:
# Create a dictionary to resample the columns from the 30min dataframe
binance_resample_dict={'Open':'first', 'High':'max', 'Low':'min', 'Close':'last', 'Volume':'sum', 'Close time':'last', 'Quote volume':'sum',
       'Number of trades':'sum', 'Taker base volume':'sum', 'Taker quote volume':'sum'}

df_data_90m = df_data_30m.resample('90min').agg(binance_resample_dict) # resample to 90 min
df_data_90m

Open     High      Low    Close       Volume  \
Open time                                                                    
2018-01-01 00:00:00+00:00   733.01   734.52   720.03   729.55   3170.31443   
2018-01-01 01:30:00+00:00   729.78   731.90   716.80   724.05   3408.01468   
2018-01-01 03:00:00+00:00   723.95   740.00   722.70   738.32   3334.66388   
2018-01-01 04:30:00+00:00   738.33   750.00   738.33   748.99   3450.77033   
2018-01-01 06:00:00+00:00   748.91   763.55   746.21   755.11   4091.23006   
...                            ...      ...      ...      ...          ...   
2022-02-25 00:00:00+00:00  2596.26  2647.94  2582.37  2631.77  43625.05550   
2022-02-25 01:30:00+00:00  2631.45  2649.96  2617.01  2639.38  32099.19590   
2022-02-25 03:00:00+00:00  2639.38  2641.51  2606.14  2625.69  28592.66100   
2022-02-25 04:30:00+00:00  2625.69  2627.73  2585.25  2606.02  26017.30240   
2022-02-25 06:00:00+00:00  2606.03  2634.80  2597.04  2620.02  10979.07900   

                                                Close time  Quote volume  \
Open time                                                                  
2018-01-01 00:00:00+00:00 2018-01-01 01:29:59.999000+00:00  2.302778e+06   
2018-01-01 01:30:00+00:00 2018-01-01 02:59:59.999000+00:00  2.465686e+06   
2018-01-01 03:00:00+00:00 2018-01-01 04:29:59.999000+00:00  2.445694e+06   
2018-01-01 04:30:00+00:00 2018-01-01 05:59:59.999000+00:00  2.572894e+06   
2018-01-01 06:00:00+00:00 2018-01-01 07:29:59.999000+00:00  3.087202e+06   
...                                                    ...           ...   
2022-02-25 00:00:00+00:00 2022-02-25 01:29:59.999000+00:00  1.139400e+08   
2022-02-25 01:30:00+00:00 2022-02-25 02:59:59.999000+00:00  8.453939e+07   
2022-02-25 03:00:00+00:00 2022-02-25 04:29:59.999000+00:00  7.508963e+07   
2022-02-25 04:30:00+00:00 2022-02-25 05:59:59.999000+00:00  6.785994e+07   
2022-02-25 06:00:00+00:00 2022-02-25 06:59:59.999000+00:00  2.873234e+07   

                           Number of trades  Taker base volume  \
Open time                                                        
2018-01-01 00:00:00+00:00              4269         1725.53798   
2018-01-01 01:30:00+00:00              4677         1764.85829   
2018-01-01 03:00:00+00:00              5435         1691.60727   
2018-01-01 04:30:00+00:00              5254         2116.02902   
2018-01-01 06:00:00+00:00              5724         2268.88235   
...                                     ...                ...   
2022-02-25 00:00:00+00:00             76438        23680.19180   
2022-02-25 01:30:00+00:00             52846        18202.02840   
2022-02-25 03:00:00+00:00             41910        13816.68630   
2022-02-25 04:30:00+00:00             46198        12292.56570   
2022-02-25 06:00:00+00:00             17395         6503.62090   

                           Taker quote volume  
Open time                                      
2018-01-01 00:00:00+00:00        1.253290e+06  
2018-01-01 01:30:00+00:00        1.277309e+06  
2018-01-01 03:00:00+00:00        1.240213e+06  
2018-01-01 04:30:00+00:00        1.577940e+06  
2018-01-01 06:00:00+00:00        1.712471e+06  
...                                       ...  
2022-02-25 00:00:00+00:00        6.186508e+07  
2022-02-25 01:30:00+00:00        4.793629e+07  
2022-02-25 03:00:00+00:00        3.629622e+07  
2022-02-25 04:30:00+00:00        3.206538e+07  
2022-02-25 06:00:00+00:00        1.702465e+07  

[24261 rows x 10 columns]

In [33]:
# Check it out to make sure everything is accurate
df_data_30m

Open     High      Low    Close       Volume  \
Open time                                                                    
2018-01-01 00:00:00+00:00   733.01   734.52   720.03   725.51   1007.73288   
2018-01-01 00:30:00+00:00   725.51   728.61   722.50   727.62   1098.16812   
2018-01-01 01:00:00+00:00   727.01   732.00   723.00   729.55   1064.41343   
2018-01-01 01:30:00+00:00   729.78   731.90   716.80   717.97   1241.55743   
2018-01-01 02:00:00+00:00   717.67   725.75   717.59   720.92   1105.27741   
...                            ...      ...      ...      ...          ...   
2022-02-25 04:30:00+00:00  2625.69  2627.73  2611.50  2616.76   6311.81210   
2022-02-25 05:00:00+00:00  2616.75  2623.53  2585.25  2606.00  13663.82490   
2022-02-25 05:30:00+00:00  2606.01  2622.85  2603.46  2606.02   6041.66540   
2022-02-25 06:00:00+00:00  2606.03  2634.80  2597.04  2622.05   9932.48080   
2022-02-25 06:30:00+00:00  2622.05  2623.13  2614.08  2620.02   1046.59820   

                                                Close time  Quote volume  \
Open time                                                                  
2018-01-01 00:00:00+00:00 2018-01-01 00:29:59.999000+00:00  7.313364e+05   
2018-01-01 00:30:00+00:00 2018-01-01 00:59:59.999000+00:00  7.972228e+05   
2018-01-01 01:00:00+00:00 2018-01-01 01:29:59.999000+00:00  7.742186e+05   
2018-01-01 01:30:00+00:00 2018-01-01 01:59:59.999000+00:00  9.015343e+05   
2018-01-01 02:00:00+00:00 2018-01-01 02:29:59.999000+00:00  7.984038e+05   
...                                                    ...           ...   
2022-02-25 04:30:00+00:00 2022-02-25 04:59:59.999000+00:00  1.652876e+07   
2022-02-25 05:00:00+00:00 2022-02-25 05:29:59.999000+00:00  3.554027e+07   
2022-02-25 05:30:00+00:00 2022-02-25 05:59:59.999000+00:00  1.579091e+07   
2022-02-25 06:00:00+00:00 2022-02-25 06:29:59.999000+00:00  2.599259e+07   
2022-02-25 06:30:00+00:00 2022-02-25 06:59:59.999000+00:00  2.739757e+06   

                           Number of trades  Taker base volume  \
Open time                                                        
2018-01-01 00:00:00+00:00              1757          562.41552   
2018-01-01 00:30:00+00:00              1357          712.81719   
2018-01-01 01:00:00+00:00              1155          450.30527   
2018-01-01 01:30:00+00:00              1720          585.02986   
2018-01-01 02:00:00+00:00              1625          615.02488   
...                                     ...                ...   
2022-02-25 04:30:00+00:00             12997         2643.90020   
2022-02-25 05:00:00+00:00             20271         6332.41660   
2022-02-25 05:30:00+00:00             12930         3316.24890   
2022-02-25 06:00:00+00:00             15253         6060.52670   
2022-02-25 06:30:00+00:00              2142          443.09420   

                           Taker quote volume  
Open time                                      
2018-01-01 00:00:00+00:00        4.079747e+05  
2018-01-01 00:30:00+00:00        5.174704e+05  
2018-01-01 01:00:00+00:00        3.278448e+05  
2018-01-01 01:30:00+00:00        4.253670e+05  
2018-01-01 02:00:00+00:00        4.443744e+05  
...                                       ...  
2022-02-25 04:30:00+00:00        6.923627e+06  
2022-02-25 05:00:00+00:00        1.647355e+07  
2022-02-25 05:30:00+00:00        8.668205e+06  
2022-02-25 06:00:00+00:00        1.586495e+07  
2022-02-25 06:30:00+00:00        1.159693e+06  

[72525 rows x 10 columns]

# Fix up the tradingview trade dataframe

In [72]:
# The following only needs to be done once after reading the trades in from tradingview and from vectorbt
# If these are pulled from pickled files then you can comment the following out

df_data_2hr.index = df_data_90m.index.tz_localize(None) # convert the index to tz-naive
df_trades_2hr.index = pd.to_datetime(df_trades_2hr.index)
df_trades_2hr.index = df_trades_2hr.index.tz_localize(None) # convert the index to tz-naive


ValueError: Length mismatch: Expected axis has 18147 elements, new values have 24261 elements

In [73]:
df_trades_2hr.index = df_trades_2hr.index.tz_localize(None) # convert the index to tz-naive
df_trades_2hr.index
df_data_2hr.index = df_data_2hr.index.tz_localize(None) # convert the index to tz-naive

In [74]:
# Have a look at the trades dataframe
df_trades_2hr
# Note the date/time should be in UTC and the price should be the "Open" price from our dataframe above or very close to it.

Trade #         Type                      Signal  \
Date/Time                                                               
2018-01-01 22:00:00        1   Entry Long                       ParLE   
2018-01-02 00:00:00        1    Exit Long                         tpL   
2018-02-17 00:00:00        2   Entry Long                       ParLE   
2018-02-18 02:00:00        2    Exit Long                       ParSE   
2018-02-18 02:00:00        3  Entry Short                       ParSE   
...                      ...          ...                         ...   
2022-02-15 08:00:00      348    Exit Long                         tpL   
2022-02-21 12:00:00      349  Entry Short                       ParSE   
2022-02-22 12:00:00      349   Exit Short  Close entry(s) order ParSE   
2022-02-22 12:00:00      350   Entry Long                       ParLE   
2022-02-23 08:00:00      350    Exit Long                         tpL   

                       Price  Contracts  Profit NONE  Profit %  \
Date/Time                                                        
2018-01-01 22:00:00   759.01    79.0222      2997.21      5.00   
2018-01-02 00:00:00   797.25    79.0222      2997.21      5.00   
2018-02-17 00:00:00   938.61    65.8360      1120.60      1.81   
2018-02-18 02:00:00   956.01    65.8360      1120.60      1.81   
2018-02-18 02:00:00   956.01    66.0511      2848.54      4.51   
...                      ...        ...          ...       ...   
2022-02-15 08:00:00  3074.62    95.7252     13942.33      4.97   
2022-02-21 12:00:00  2626.77   108.6675      3952.97      1.38   
2022-02-22 12:00:00  2589.35   108.6675      3952.97      1.38   
2022-02-22 12:00:00  2589.35   219.8348     28228.63      4.96   
2022-02-23 08:00:00  2718.82   219.8348     28228.63      4.96   

                     Cum. Profit NONE  Cum. Profit %  Run-up NONE  Run-up %  \
Date/Time                                                                     
2018-01-01 22:00:00           2997.21           3.00      3009.81      5.02   
2018-01-02 00:00:00           2997.21           3.00      3009.81      5.02   
2018-02-17 00:00:00           4117.81           1.09      2613.84      4.23   
2018-02-18 02:00:00           4117.81           1.09      2613.84      4.23   
2018-02-18 02:00:00           6966.35           2.74      2892.30      4.58   
...                               ...            ...          ...       ...   
2022-02-15 08:00:00         375742.88           3.02     14001.19      5.00   
2022-02-21 12:00:00         379695.84           0.83     13718.69      4.81   
2022-02-22 12:00:00         379695.84           0.83     13718.69      4.81   
2022-02-22 12:00:00         407924.47           5.88     28348.17      4.98   
2022-02-23 08:00:00         407924.47           5.88     28348.17      4.98   

                     Drawdown NONE  Drawdown %  Close Price  Open Price  
Date/Time                                                                
2018-01-01 22:00:00         798.27        1.33          NaN         NaN  
2018-01-02 00:00:00         798.27        1.33          NaN         NaN  
2018-02-17 00:00:00         350.10        0.57          NaN         NaN  
2018-02-18 02:00:00         350.10        0.57          NaN         NaN  
2018-02-18 02:00:00          32.44        0.05          NaN         NaN  
...                            ...         ...          ...         ...  
2022-02-15 08:00:00        6803.72        2.43          NaN         NaN  
2022-02-21 12:00:00       13543.81        4.74          NaN         NaN  
2022-02-22 12:00:00       13543.81        4.74          NaN         NaN  
2022-02-22 12:00:00        5139.27        0.90          NaN         NaN  
2022-02-23 08:00:00        5139.27        0.90          NaN         NaN  

[700 rows x 15 columns]

In [75]:
df_data_2hr

Open     High      Low    Close       Volume  \
Open time                                                              
2018-01-01 00:00:00   733.01   734.52   716.80   717.97   4411.87186   
2018-01-01 02:00:00   717.67   737.99   717.59   734.50   4327.36175   
2018-01-01 04:00:00   734.99   750.00   730.01   748.99   4624.52971   
2018-01-01 06:00:00   748.91   763.55   746.21   751.99   4867.81763   
2018-01-01 08:00:00   751.77   758.10   737.40   753.21   4202.06918   
...                      ...      ...      ...      ...          ...   
2022-02-24 22:00:00  2635.73  2644.12  2544.44  2596.20  46416.42290   
2022-02-25 00:00:00  2596.26  2647.94  2582.37  2629.87  53212.83410   
2022-02-25 02:00:00  2629.86  2649.96  2606.14  2636.92  43362.69960   
2022-02-25 04:00:00  2636.92  2639.00  2585.25  2606.02  33758.68110   
2022-02-25 06:00:00  2606.03  2634.80  2597.04  2622.43  11089.94940   

                                          Close time  Quote volume  \
Open time                                                            
2018-01-01 00:00:00 2018-01-01 01:59:59.999000+00:00  3.204312e+06   
2018-01-01 02:00:00 2018-01-01 03:59:59.999000+00:00  3.146352e+06   
2018-01-01 04:00:00 2018-01-01 05:59:59.999000+00:00  3.436388e+06   
2018-01-01 06:00:00 2018-01-01 07:59:59.999000+00:00  3.672219e+06   
2018-01-01 08:00:00 2018-01-01 09:59:59.999000+00:00  3.146660e+06   
...                                              ...           ...   
2022-02-24 22:00:00 2022-02-24 23:59:59.999000+00:00  1.202482e+08   
2022-02-25 00:00:00 2022-02-25 01:59:59.999000+00:00  1.391146e+08   
2022-02-25 02:00:00 2022-02-25 03:59:59.999000+00:00  1.141071e+08   
2022-02-25 04:00:00 2022-02-25 05:59:59.999000+00:00  8.820727e+07   
2022-02-25 06:00:00 2022-02-25 07:59:59.999000+00:00  2.902299e+07   

                     Number of trades  Taker base volume  Taker quote volume  
Open time                                                                     
2018-01-01 00:00:00              5989         2310.56784        1.678657e+06  
2018-01-01 02:00:00              6604         2275.46114        1.653412e+06  
2018-01-01 04:00:00              7042         2712.00358        2.016683e+06  
2018-01-01 06:00:00              6867         2576.52968        1.944414e+06  
2018-01-01 08:00:00              5593         2051.95665        1.537156e+06  
...                               ...                ...                 ...  
2022-02-24 22:00:00            108100        21189.47650        5.491843e+07  
2022-02-25 00:00:00             92951        29099.42390        7.609428e+07  
2022-02-25 02:00:00             65855        22529.94380        5.930515e+07  
2022-02-25 04:00:00             58586        16362.10450        4.276353e+07  
2022-02-25 06:00:00             17616         6575.46400        1.721296e+07  

[18147 rows x 10 columns]

In [76]:
# Let's try adding the close price and open prices to the trades dataframe. We might need them later.
df_trades_2hr["Close Price"] = df_data_2hr["Close"]
df_trades_2hr["Open Price"] = df_data_2hr["Open"]



In [77]:
df_data_2hr.index

DatetimeIndex(['2018-01-01 00:00:00', '2018-01-01 02:00:00',
               '2018-01-01 04:00:00', '2018-01-01 06:00:00',
               '2018-01-01 08:00:00', '2018-01-01 10:00:00',
               '2018-01-01 12:00:00', '2018-01-01 14:00:00',
               '2018-01-01 16:00:00', '2018-01-01 18:00:00',
               ...
               '2022-02-24 12:00:00', '2022-02-24 14:00:00',
               '2022-02-24 16:00:00', '2022-02-24 18:00:00',
               '2022-02-24 20:00:00', '2022-02-24 22:00:00',
               '2022-02-25 00:00:00', '2022-02-25 02:00:00',
               '2022-02-25 04:00:00', '2022-02-25 06:00:00'],
              dtype='datetime64[ns]', name='Open time', length=18147, freq=None)

In [78]:
# df_combined  = pd.concat([df_data_90m, df_trades_2hr]).sort_index()
df_combined  = pd.concat([df_data_2hr, df_trades_2hr]).sort_index()

In [49]:
print(df_data_2hr.shape)
print(df_trades_2hr.shape)
test = pd.merge(df_data_2hr, df_trades_2hr, how='left', left_index=True, right_index=True)

(18147, 10)
(700, 16)


In [79]:
test.shape

(18147, 26)

In [80]:
# combine data and trades 

df_combined  = pd.concat([df_data_2hr, df_trades_2hr]).sort_index()

df_combined = df_combined[["Close","Open","Open Price","Price","Type","Contracts"]]
df_combined.loc["2018-01-05"]

Close     Open  Open Price  Price Type  Contracts
2018-01-05 00:00:00   978.10   940.00         NaN    NaN  NaN        NaN
2018-01-05 02:00:00  1003.01   979.14         NaN    NaN  NaN        NaN
2018-01-05 04:00:00  1008.99  1003.01         NaN    NaN  NaN        NaN
2018-01-05 06:00:00  1030.00  1009.73         NaN    NaN  NaN        NaN
2018-01-05 08:00:00   991.87  1029.12         NaN    NaN  NaN        NaN
2018-01-05 10:00:00   995.98   993.98         NaN    NaN  NaN        NaN
2018-01-05 12:00:00   978.09   995.90         NaN    NaN  NaN        NaN
2018-01-05 14:00:00   981.50   979.98         NaN    NaN  NaN        NaN
2018-01-05 16:00:00   944.80   981.11         NaN    NaN  NaN        NaN
2018-01-05 18:00:00   970.80   944.81         NaN    NaN  NaN        NaN
2018-01-05 20:00:00   951.78   970.81         NaN    NaN  NaN        NaN
2018-01-05 22:00:00   959.30   950.99         NaN    NaN  NaN        NaN

In [81]:
# This creates the boolean for the signals
df_combined["entries"] = df_combined["Type"] == "Entry Long"
df_combined["exits"] = df_combined["Type"] == "Exit Long"
df_combined["size"] = df_combined["Contracts"]
df_combined["short_entries"] = df_combined["Type"] == "Entry Short"
df_combined["short_exits"] = df_combined["Type"] == "Exit Short"
df_combined

Close     Open  Open Price  Price Type  Contracts  \
2018-01-01 00:00:00   717.97   733.01         NaN    NaN  NaN        NaN   
2018-01-01 02:00:00   734.50   717.67         NaN    NaN  NaN        NaN   
2018-01-01 04:00:00   748.99   734.99         NaN    NaN  NaN        NaN   
2018-01-01 06:00:00   751.99   748.91         NaN    NaN  NaN        NaN   
2018-01-01 08:00:00   753.21   751.77         NaN    NaN  NaN        NaN   
...                      ...      ...         ...    ...  ...        ...   
2022-02-24 22:00:00  2596.20  2635.73         NaN    NaN  NaN        NaN   
2022-02-25 00:00:00  2629.87  2596.26         NaN    NaN  NaN        NaN   
2022-02-25 02:00:00  2636.92  2629.86         NaN    NaN  NaN        NaN   
2022-02-25 04:00:00  2606.02  2636.92         NaN    NaN  NaN        NaN   
2022-02-25 06:00:00  2622.43  2606.03         NaN    NaN  NaN        NaN   

                     entries  exits  size  short_entries  short_exits  
2018-01-01 00:00:00    False  False   NaN          False        False  
2018-01-01 02:00:00    False  False   NaN          False        False  
2018-01-01 04:00:00    False  False   NaN          False        False  
2018-01-01 06:00:00    False  False   NaN          False        False  
2018-01-01 08:00:00    False  False   NaN          False        False  
...                      ...    ...   ...            ...          ...  
2022-02-24 22:00:00    False  False   NaN          False        False  
2022-02-25 00:00:00    False  False   NaN          False        False  
2022-02-25 02:00:00    False  False   NaN          False        False  
2022-02-25 04:00:00    False  False   NaN          False        False  
2022-02-25 06:00:00    False  False   NaN          False        False  

[18847 rows x 11 columns]

In [82]:

df_combined["Close"].fillna(df_combined["Open Price"], inplace=True) # fill in the missing close prices with the open price from the trades dataframe

In [83]:
df_combined.loc["2018-01-05"] # Take a look on a day where multiple trades took place

Close     Open  Open Price  Price Type  Contracts  \
2018-01-05 00:00:00   978.10   940.00         NaN    NaN  NaN        NaN   
2018-01-05 02:00:00  1003.01   979.14         NaN    NaN  NaN        NaN   
2018-01-05 04:00:00  1008.99  1003.01         NaN    NaN  NaN        NaN   
2018-01-05 06:00:00  1030.00  1009.73         NaN    NaN  NaN        NaN   
2018-01-05 08:00:00   991.87  1029.12         NaN    NaN  NaN        NaN   
2018-01-05 10:00:00   995.98   993.98         NaN    NaN  NaN        NaN   
2018-01-05 12:00:00   978.09   995.90         NaN    NaN  NaN        NaN   
2018-01-05 14:00:00   981.50   979.98         NaN    NaN  NaN        NaN   
2018-01-05 16:00:00   944.80   981.11         NaN    NaN  NaN        NaN   
2018-01-05 18:00:00   970.80   944.81         NaN    NaN  NaN        NaN   
2018-01-05 20:00:00   951.78   970.81         NaN    NaN  NaN        NaN   
2018-01-05 22:00:00   959.30   950.99         NaN    NaN  NaN        NaN   

                     entries  exits  size  short_entries  short_exits  
2018-01-05 00:00:00    False  False   NaN          False        False  
2018-01-05 02:00:00    False  False   NaN          False        False  
2018-01-05 04:00:00    False  False   NaN          False        False  
2018-01-05 06:00:00    False  False   NaN          False        False  
2018-01-05 08:00:00    False  False   NaN          False        False  
2018-01-05 10:00:00    False  False   NaN          False        False  
2018-01-05 12:00:00    False  False   NaN          False        False  
2018-01-05 14:00:00    False  False   NaN          False        False  
2018-01-05 16:00:00    False  False   NaN          False        False  
2018-01-05 18:00:00    False  False   NaN          False        False  
2018-01-05 20:00:00    False  False   NaN          False        False  
2018-01-05 22:00:00    False  False   NaN          False        False

# Note above that this is not perfect. open vs closed and such.

In [84]:
# Show all of the rows where either a long or short entry trade took place
mask = df_combined[(df_combined["short_entries"] == True) | (df_combined["entries"] == True)]
# Create a Mask for simplified searching
mask.index
# Test out the ability to set opening values as main value for the vectorbt strategy, 
new_df = df_combined.loc[mask.index]
new_df["Open"] = df_data_90m["Open"]


In [85]:
new_df

Close     Open  Open Price    Price         Type  \
2018-01-01 22:00:00   759.00      NaN      759.00   759.01   Entry Long   
2018-01-01 22:00:00   754.99      NaN         NaN      NaN          NaN   
2018-02-17 00:00:00   938.60   938.60      938.60   938.61   Entry Long   
2018-02-17 00:00:00   947.79   938.60         NaN      NaN          NaN   
2018-02-18 02:00:00   952.20      NaN         NaN      NaN          NaN   
...                      ...      ...         ...      ...          ...   
2022-02-21 12:00:00  2606.86  2626.78         NaN      NaN          NaN   
2022-02-21 12:00:00  2626.78  2626.78     2626.78  2626.77  Entry Short   
2022-02-22 12:00:00  2589.34  2589.34     2589.34  2589.35   Exit Short   
2022-02-22 12:00:00  2589.34  2589.34     2589.34  2589.35   Entry Long   
2022-02-22 12:00:00  2612.75  2589.34         NaN      NaN          NaN   

                     Contracts  entries  exits      size  short_entries  \
2018-01-01 22:00:00    79.0222     True  False   79.0222          False   
2018-01-01 22:00:00        NaN    False  False       NaN          False   
2018-02-17 00:00:00    65.8360     True  False   65.8360          False   
2018-02-17 00:00:00        NaN    False  False       NaN          False   
2018-02-18 02:00:00        NaN    False  False       NaN          False   
...                        ...      ...    ...       ...            ...   
2022-02-21 12:00:00        NaN    False  False       NaN          False   
2022-02-21 12:00:00   108.6675    False  False  108.6675           True   
2022-02-22 12:00:00   108.6675    False  False  108.6675          False   
2022-02-22 12:00:00   219.8348     True  False  219.8348          False   
2022-02-22 12:00:00        NaN    False  False       NaN          False   

                     short_exits  
2018-01-01 22:00:00        False  
2018-01-01 22:00:00        False  
2018-02-17 00:00:00        False  
2018-02-17 00:00:00        False  
2018-02-18 02:00:00        False  
...                          ...  
2022-02-21 12:00:00        False  
2022-02-21 12:00:00        False  
2022-02-22 12:00:00         True  
2022-02-22 12:00:00        False  
2022-02-22 12:00:00        False  

[952 rows x 11 columns]

In [86]:
# Show the Long and Short signals
print(df_combined["entries"].value_counts())
print(df_combined["short_entries"].value_counts())


False    18670
True       177
Name: entries, dtype: int64
False    18674
True       173
Name: short_entries, dtype: int64


In [87]:
# Create the portfolio object

portfolio = vbt.Portfolio.from_signals(df_combined["Close"], 
                                        entries=df_combined["entries"].to_list(), 
                                        exits=df_combined["exits"].to_list(), 
                                        size=df_combined["size"].to_list(),
                                        short_entries=df_combined["short_entries"].to_list(), 
                                        short_exits=df_combined["short_exits"].to_list(), 
                                        price=df_combined['Close'].to_list(),
                                        )

In [88]:
# Show the positions and trades in a readable format
portfolio.positions.records_readable

Position Id Column        Size     Entry Timestamp  Avg Entry Price  \
0              0  Close   79.022200 2018-01-01 22:00:00           759.00   
1              1  Close   65.836000 2018-02-17 00:00:00           938.60   
2              2  Close   66.051100 2018-02-18 02:00:00           972.91   
3              3  Close   75.141400 2018-03-03 22:00:00           854.12   
4              4  Close   74.938700 2018-03-04 12:00:00           849.22   
..           ...    ...         ...                 ...              ...   
342          342  Close   96.573400 2022-02-12 20:00:00          2952.50   
343          343  Close   98.204000 2022-02-13 16:00:00          2919.75   
344          344  Close   95.725200 2022-02-14 12:00:00          2874.39   
345          345  Close  108.667500 2022-02-21 12:00:00          2626.78   
346          346  Close  167.566859 2022-02-22 12:00:00          2589.34   

      Entry Fees      Exit Timestamp  Avg Exit Price    Exit Fees  \
0     149.944625 2018-01-02 00:00:00          754.99   149.152427   
1     154.484174 2018-02-18 02:00:00          972.91   160.131257   
2     160.654439 2018-02-18 06:00:00          912.50   150.679072   
3     160.449431 2018-03-04 12:00:00          849.22   159.528949   
4     159.098607 2018-03-05 14:00:00          866.37   162.311604   
..           ...                 ...             ...          ...   
342   712.832409 2022-02-13 16:00:00         2919.75   704.925462   
343   716.827822 2022-02-14 12:00:00         2874.39   705.691489   
344   687.878894 2022-02-15 08:00:00         3049.44   729.770635   
345   713.614039 2022-02-22 12:00:00         2589.34   703.442761   
346  1084.718929 2022-02-23 08:00:00         2695.62  1129.241444   

              PnL    Return Direction  Status  
0     -615.976073 -0.010270      Long  Closed  
1     1944.217729  0.031463      Long  Closed  
2     3678.813440  0.057247     Short  Closed  
3       48.214479  0.000751     Short  Closed  
4      963.788494  0.015145      Long  Closed  
..            ...       ...       ...     ...  
342  -4580.536720 -0.016065      Long  Closed  
343   3032.014129  0.010574     Short  Closed  
344  15339.046731  0.055748      Long  Closed  
345   2651.454400  0.009289     Short  Closed  
346  15595.045445  0.035943      Long  Closed  

[347 rows x 13 columns]

In [89]:
portfolio.positions.records_readable.columns

Index(['Position Id', 'Column', 'Size', 'Entry Timestamp', 'Avg Entry Price',
       'Entry Fees', 'Exit Timestamp', 'Avg Exit Price', 'Exit Fees', 'PnL',
       'Return', 'Direction', 'Status'],
      dtype='object')

In [90]:
portfolio.positions.records_readable["Direction"]

0       Long
1       Long
2      Short
3      Short
4       Long
       ...  
342     Long
343    Short
344     Long
345    Short
346     Long
Name: Direction, Length: 347, dtype: object

In [92]:
# Show the Long and Short signals to the portfolio 
print("VectorBT thinks the portfolio has the following long and short signals: ")
print(portfolio.positions.records_readable["Direction"].value_counts()) # Check the vectorbt portfolio trades 

print("The Input Dataframe had the following information: ")
print("The Long signals are:")
print(df_combined["entries"].value_counts())

print("The Short signals are:")
print(df_combined["short_entries"].value_counts())

print("The original trades from the tradingview file are:")
print(df_trades_2hr["Type"].value_counts())

VectorBT thinks the portfolio has the following long and short signals: 
Long     175
Short    172
Name: Direction, dtype: int64
The Input Dataframe had the following information: 
The Long signals are:
False    18670
True       177
Name: entries, dtype: int64
The Short signals are:
False    18674
True       173
Name: short_entries, dtype: int64
The original trades from the tradingview file are:
Exit Long      177
Entry Long     177
Entry Short    173
Exit Short     173
Name: Type, dtype: int64


# Let's look at the results from VectorBT

In [93]:
# Show the portfolio statistics and compare the returns of the banchmark
bm_rets_90m = df_combined["Close"].vbt.to_returns() # create returns dataframe for the benchmark
portfolio.stats(settings=dict(benchmark_returns=bm_rets_90m, # Sets the benchmark returns for stats comparisons
                              frequency='90min', # Sets the frequency for stats comparisons
                              )
                )

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sharpe_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'calmar_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'omega_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sortino_ratio' requires frequency to be set
  warnings.warn(warning_message)


Start                         2018-01-01 00:00:00
End                           2022-02-25 06:00:00
Period                                      18847
Start Value                              100000.0
End Value                           450567.336115
Total Return [%]                       350.567336
Benchmark Return [%]                   265.256208
Max Gross Exposure [%]              439096.650302
Total Fees Paid                     291597.635715
Max Drawdown [%]                        12.528313
Max Drawdown Duration                      1520.0
Total Trades                                  347
Total Closed Trades                           347
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                            58.213256
Best Trade [%]                          21.077347
Worst Trade [%]                         -7.166716
Avg Winning Trade [%]                    2.306814
Avg Losing Trade [%]                    -1.395409


In [94]:
print(portfolio.stats(settings=dict(benchmark_returns=bm_rets_90m, # Sets the benchmark returns for stats comparisons
                              frequency='90min', # Sets the frequency for stats comparisons
                              )
                )
      )
portfolio.plot().show()

/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sharpe_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'calmar_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'omega_ratio' requires frequency to be set
  warnings.warn(warning_message)
/Users/ericervin/anaconda3/envs/data-science/lib/python3.8/site-packages/vectorbt/generic/stats_builder.py:397: UserWarning: Metric 'sortino_ratio' requires frequency to be set
  warnings.warn(warning_message)


Start                         2018-01-01 00:00:00
End                           2022-02-25 06:00:00
Period                                      18847
Start Value                              100000.0
End Value                           450567.336115
Total Return [%]                       350.567336
Benchmark Return [%]                   265.256208
Max Gross Exposure [%]              439096.650302
Total Fees Paid                     291597.635715
Max Drawdown [%]                        12.528313
Max Drawdown Duration                      1520.0
Total Trades                                  347
Total Closed Trades                           347
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                            58.213256
Best Trade [%]                          21.077347
Worst Trade [%]                         -7.166716
Avg Winning Trade [%]                    2.306814
Avg Losing Trade [%]                    -1.395409


# Now time to introduce Quantstats tearsheets

In [95]:
import quantstats as qs

In [ ]:
qs.